In [1]:
# Original challenge.py
import hashlib
import struct

class CustomSHA:
    def __init__(self, data: bytes):
        self.data: bytes = data

    def process(self) -> str:
        h0 = 0x674523EFCD.to_bytes(5, byteorder='big')
        h = h0
        data = self.preprocess()

        for i in range(0, len(data), 8):
            chunk = data[i:i+8]

            h = hashlib.sha256(chunk + h).digest()[:5]

        return f'{h.hex()}'

    def preprocess(self) -> bytes:
        data = self.data
        data = bytearray(data)

        data.append(0x80)
        while len(data) % 8 != 0:
            data.append(0x00)

        data += struct.pack('>Q', 8 * len(self.data))

        return bytes(data)


    def sha_custom(self):
        return self.process()

with open("Hack.zip", "rb") as f:
    data_hack = f.read()
    CustomSHA(data_hack)
    sha_custom_hack = CustomSHA(data_hack).sha_custom()

def challenge(received_json):
    response_json = {}
    if 'action' in received_json:
        if received_json['action'] == 'hash':
            if 'data' in received_json:
                data = bytes.fromhex(received_json['data'])
                if data == data_hack:
                    response_json['error'] = "Forbidden data"
                else:
                    sha_custom = CustomSHA(data)
                    response_json['hash'] = sha_custom.sha_custom()

                    if sha_custom_hack == response_json['hash']:
                        response_json['flag'] = FLAG
            else:
                response_json['error'] = 'No data provided'
        else:
            response_json['error'] = 'Invalid action'
    else:
        response_json['error'] = 'No action provided'

    return response_json


In [2]:
print(sha_custom_hack)

d8e3e7c169


In [6]:
# Compute all the intermediate hashes h_i for a given data string
def compute_chain_h(data):
    data = bytearray(data)
    hs = []

    h0 = 0x674523EFCD.to_bytes(5, byteorder='big')
    h = h0
    hs.append(h0)

    for i in range(0, len(data), 8):
        chunk = data[i:i+8]

        h = hashlib.sha256(chunk + h).digest()[:5]
        hs.append(h)

    return hs

hshack = compute_chain_h(data_hack)

In [4]:
"""
Finds a buffer of size length, such that it hashes to one of the values in hs (starting from hstart)
"""
def find_collision(hstart, hs, length = 1):
    buf = bytearray()
    hset = set(hs)

    h = hstart
    i = 0
    for i in range(length-1):
        chunk = bytearray(8)
        buf += chunk
        i += 1
        h = hashlib.sha256(chunk + h).digest()[:5]

    i=0
    while True:
        chunk = bytearray(i.to_bytes(8, byteorder='big'))
        i += 1
        h2 = hashlib.sha256(chunk + h).digest()[:5]
        if h2 in hset:
            buf += chunk
            return buf, hs.index(h2)

In [10]:
# Now, we find several independent modifications of the file that reduces/extends its size
# We want them to apply to disjoint sets of (h_i) to be able to apply them independently later
intervals = []
index0 = 0
for j in range(18):
    buf, index = find_collision(hshack[index0], hshack[index0:index0+20000], length=10000)
    intervals.append((index0, index0+index, buf))
    index0 += index
    print(25000-index)

-3367
-2767
3435
-4605
-7649
-7345
245
-5974
-8524
-689
7603
4968
-8475
-8854
2893
-9943
-4385
-779


In [13]:
# In this code, we look for a subset of modifications that does not alter the file size
# To do so, we solve the Subset Sum problem for the above integers.
diffs = []
for (i0, i1, buf) in intervals:
    diffs.append(len(buf)//8 - (i1-i0))

sums = set()
sols = dict()
for i, v in enumerate(diffs):
    for u in list(sums):
        sums.add(u+v)
        sols[u+v] = sols[u].copy()
        sols[u+v].add(i)
    sums.add(v)
    sols[v] = set([i])
    
sol = list(sols[0])
sol.sort()
print(sol)

[1, 2, 10, 11, 13, 16]


In [16]:
# Now, we apply the selected modifications to Hack.zip
def replace_chain(data, v):
    (i0, i1, buf) = v
    databis = data[:i0*8] + buf + data[i1*8:]
    hsbis = compute_chain_h(databis)
    print(hsbis[-1].hex(), hshack[-1].hex())
    print(len(databis)/8, len(data_hack)/8)
    return databis

datafin = data_hack[:]
for i in sol[::-1]:
    datafin = replace_chain(datafin, intervals[i])

e2c3cc7202 e2c3cc7202
1922930.125 1927315.125
e2c3cc7202 e2c3cc7202
1914076.125 1927315.125
e2c3cc7202 e2c3cc7202
1919044.125 1927315.125
e2c3cc7202 e2c3cc7202
1926647.125 1927315.125
e2c3cc7202 e2c3cc7202
1930082.125 1927315.125
e2c3cc7202 e2c3cc7202
1927315.125 1927315.125


In [17]:
# And we produce the string expected by challenge.py
data_hack2 = bytes(datafin)

import json

j = {
    "action":"hash",
    "data": data_hack2.hex()
}

# Serializing json
json_object = json.dumps(j)
with open("response.json", "w") as outfile:
    outfile.write(json_object)